# TREXIO->TurboRVB conversion using pyturbo

In [25]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [26]:
# import python modules
import os,sys
import shutil
import numpy as np
import os
import pandas as pd
import subprocess
from subprocess import PIPE

In [27]:
# import trexio - python wrapper
import trexio

In [28]:
# import turbo-genius modules
from pyturbo.structure import Structure
from pyturbo.pseudopotentials import Pseudopotentials
from pyturbo.basis_set import Det_Basis_sets, Jas_Basis_sets
from pyturbo.io_fort10 import IO_fort10
from pyturbo.makefort10 import Makefort10
from pyturbo.convertfort10mol import Convertfort10mol
from pyturbo.vmc import VMC

from pyturbo.utils.utility import return_atomic_number
from pyturbo.utils.utility import turbo_prim_orb_type_num, turbo_cont_orb_type_num, return_orbchr

In [29]:
os.environ["DYLD_LIBRARY_PATH"]=os.environ["LIBRARY_PATH"]

In [56]:
# prefix and file names
hdf5_filename="water.hdf5"
file_r = trexio.File(os.path.join(hdf5_filename), mode='r', back_end=trexio.TREXIO_HDF5)

In [59]:
# read electron num
num_ele_up = trexio.read_electron_up_num(file_r)
num_ele_dn = trexio.read_electron_up_num(file_r)
num_ele_total = num_ele_up + num_ele_dn

In [31]:
# read structure info.
nucleus_num_r = trexio.read_nucleus_num(file_r)
labels_r = trexio.read_nucleus_label(file_r)
charges_r = trexio.read_nucleus_charge(file_r)
coords_r = trexio.read_nucleus_coord(file_r)

atomic_number_list=[return_atomic_number(Z) for Z in labels_r]
atomic_number_unique=list(set(atomic_number_list))

In [32]:
# check data
print(f"nucleus_num from {hdf5_filename} file ---> {nucleus_num_r}")
print(f"nucleus_label from {hdf5_filename} file \n---> {labels_r}")
print(f"nucleus_charge from {hdf5_filename} file \n---> {charges_r}")
print(f"nucleus_coord from {hdf5_filename} TREXIO file: \n{coords_r}")

nucleus_num from water.hdf5 file ---> 3
nucleus_label from water.hdf5 file 
---> ['O', 'H', 'H']
nucleus_charge from water.hdf5 file 
---> [6. 1. 1.]
nucleus_coord from water.hdf5 TREXIO file: 
[[ 9.44863062 13.50601812 14.45823978]
 [ 7.6875306  13.12032124 14.29343676]
 [10.16717442 13.03337116 12.86522522]]


In [33]:
# structure
structure=Structure(
                 atomic_numbers=atomic_number_list,
                 element_symbols=labels_r,
                 positions=coords_r
                 )

In [34]:
# view
#from ase.visualize import view
#atom=structure.get_ase_atom()
#view(atom)

In [35]:
# Reading basis sets info
basis_type=trexio.read_basis_type(file_r)
basis_shell_num=trexio.read_basis_shell_num(file_r)
basis_shell_index=trexio.read_basis_shell_index(file_r)
basis_prim_num=trexio.read_basis_prim_num(file_r)
basis_nucleus_index=trexio.read_basis_nucleus_index(file_r)
basis_shell_ang_mom=trexio.read_basis_shell_ang_mom(file_r)
basis_shell_factor=trexio.read_basis_shell_factor(file_r)
basis_shell_index=trexio.read_basis_shell_index(file_r)
basis_exponent=trexio.read_basis_exponent(file_r)
basis_coefficient=trexio.read_basis_coefficient(file_r)
basis_prim_factor=trexio.read_basis_prim_factor(file_r)

# Pseudo potentials info
ecp_max_ang_mom_plus_1=trexio.read_ecp_max_ang_mom_plus_1(file_r)
ecp_z_core=trexio.read_ecp_z_core(file_r)
ecp_num=trexio.read_ecp_num(file_r)
ecp_ang_mom=trexio.read_ecp_ang_mom(file_r)
ecp_nucleus_index=trexio.read_ecp_nucleus_index(file_r)
ecp_exponent=trexio.read_ecp_exponent(file_r)
ecp_coefficient=trexio.read_ecp_coefficient(file_r)
ecp_power=trexio.read_ecp_power(file_r)

# ao info
ao_cartesian=trexio.read_ao_cartesian(file_r)
ao_num=trexio.read_ao_num(file_r)
ao_shell=trexio.read_ao_shell(file_r)
ao_normalization=trexio.read_ao_normalization(file_r)

# mo info
mo_type=trexio.read_mo_type(file_r)
mo_num=trexio.read_mo_num(file_r)
mo_coefficient=trexio.read_mo_coefficient(file_r)
#mo_occupation=trexio.read_mo_occupation(file_r)

In [36]:
print(ecp_max_ang_mom_plus_1)
print(ecp_z_core)
print(ecp_num)
print(ecp_ang_mom)
print(ecp_nucleus_index)
print(ecp_exponent)
print(ecp_coefficient)
print(ecp_power)

[2 2 2]
[2 0 0]
13
[1 1 1 0 0 1 1 1 0 1 1 1 0]
[0 0 0 0 0 1 1 1 1 2 2 2 2]
[12.30997    13.71419    14.76962    13.65512     1.         21.24359508
 21.77696655 21.24359508  1.         21.24359508 21.77696655 21.24359508
  1.        ]
[  6.         -47.876       73.85984     85.86406      0.
   1.         -10.85192405  21.24359508   0.           1.
 -10.85192405  21.24359508   0.        ]
[-1  0  1  0  0 -1  0  1  0 -1  0  1  0]


In [37]:
# basis sets
shell_ang_mom_turbo_notation = []

for i, ang_mom in enumerate(basis_shell_ang_mom):
    if list(basis_shell_index).count(i) > 1: # contracted orbitals
        shell_ang_mom_turbo_notation.append(turbo_cont_orb_type_num(return_orbchr(ang_mom)))
    else: # uncontracted orbitals
        shell_ang_mom_turbo_notation.append(turbo_prim_orb_type_num(return_orbchr(ang_mom)))
        
                        
det_basis_sets = Det_Basis_sets(
                 nucleus_index=basis_nucleus_index,
                 shell_ang_mom=basis_shell_ang_mom,
                 shell_ang_mom_turbo_notation=shell_ang_mom_turbo_notation,
                 shell_factor=basis_shell_factor,
                 shell_index=basis_shell_index,
                 exponent=basis_exponent,
                 coefficient=basis_coefficient,
                 prim_factor=basis_prim_factor,
                 )

In [38]:
# Pseudopotentials
cutoff = [0.0] * len(ecp_z_core)
pseudopotentials=Pseudopotentials(
                 max_ang_mom_plus_1=ecp_max_ang_mom_plus_1,
                 z_core=ecp_z_core,
                 cutoff=cutoff,
                 nucleus_index=ecp_nucleus_index,
                 ang_mom=ecp_ang_mom,
                 exponent=ecp_exponent,
                 coefficient=ecp_coefficient,
                 power=ecp_power
                 )
pseudopotentials.set_cutoffs()
print(pseudopotentials.cutoff)
pseudopotentials.write_pseudopotential_turborvb_file()

[1.08, 0.8, 0.8]


In [75]:
namelist = Makefort10.read_default_namelist(structure=structure, jastrow_type=0)

makefort10 = Makefort10(
    structure=structure,
    det_basis_sets=det_basis_sets,
    pseudo_potentials=pseudopotentials,
    namelist=namelist
)
makefort10.generate_input('makefort10.input')
makefort10.run()

Turbo-Genius.utils.utility - DEBUG - 115 - variable='bohr'
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable=0
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=0
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=.false.
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable=.false.
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable=.false.
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable='normal'
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable='normal'
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable=-6
Turbo-

Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 1.331816
Turbo-Genius.pyturbo.makefort10 - DEBUG - 159 - 1.0000000000000002
Turbo-Genius.pyturbo.makefort10 - DEBUG - 153 - Uncontracted shell!
Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 0.678626
Turbo-Genius.pyturbo.makefort10 - DEBUG - 159 - 1.0
Turbo-Genius.pyturbo.makefort10 - DEBUG - 153 - Uncontracted shell!
Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 0.333673
Turbo-Genius.pyturbo.makefort10 - DEBUG - 159 - 1.0
Turbo-Genius.pyturbo.makefort10 - DEBUG - 153 - Uncontracted shell!
Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 0.167017
Turbo-Genius.pyturbo.makefort10 - DEBUG - 159 - 1.0
Turbo-Genius.pyturbo.makefort10 - DEBUG - 153 - Uncontracted shell!
Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 0.083598
Turbo-Genius.pyturbo.makefort10 - DEBUG - 159 - 1.0
Turbo-Genius.pyturbo.makefort10 - DEBUG - 153 - Uncontracted shell!
Turbo-Genius.pyturbo.makefort10 - DEBUG - 158 - 0.600621
Turbo-Genius.pyturbo.makefort10 - DEBUG - 1

In [76]:
# rename fort.10
shutil.move("fort.10_new", "fort.10_in")

'fort.10_in'

In [77]:
# in_convertfort10mol class
convertfort10mol = Convertfort10mol.parse_from_default_namelist()
convertfort10mol.set_parameter("only_molecular", '.true.', "&control")
convertfort10mol.set_parameter("nmol", mo_num, "&molec_info")
convertfort10mol.set_parameter("nmolmax", num_ele_dn, "&molec_info")
convertfort10mol.generate_input()
convertfort10mol.run()

Turbo-Genius.utils.utility - DEBUG - 115 - variable=-1e-14
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.utils.utility - DEBUG - 115 - variable=100
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=100
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=100
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=30
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=30
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=43
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=1
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application

In [78]:
# rename and remove
shutil.move("fort.10_new", "fort.10")
os.remove("fort.10_in")

In [79]:
# and read and write MOs to fort.10_new -> fort.10_new_mo
io_fort10=IO_fort10(f"fort.10")

Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_genius_dist/tests/trexio_to_turborvb/fort.10
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_genius_dist/tests/trexio_to_turborvb/fort.10
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_genius_dist/tests/trexio_to_turborvb/fort.10
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_genius_dist/tests/trexio_to_turborvb/fort.10
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_genius_dist/tests/trexio_to_turborvb/fort.10
Turbo-Genius.utils.utility - DEBUG - 343 - /Users/maezono/Dropbox/98Private/00application/TurboRVB_turbogenius_refactoring/turbo_g

In [80]:
# check cartesian / spherical flag:
if ao_cartesian!=0:
    print("basis set is represent with cartesian")
else:
    print("basis set is represent with spherical")

mo_coefficient_turbo=[]
num=mo_num
#num=1
for mo_i in range(num):
    print(f"============{mo_i+1}-th MO================")
    mo_coefficient_list=[]
    #print(f"i={i}")
    #print(mo_coefficient[i])
    #print(ao_shell)
    
    for ao_i, ao_index in enumerate(ao_shell):
        print(f"--ao_i={ao_i}, ao_index={ao_index}--")
        # for real spherical harmonic notations, 
        # see [https://en.wikipedia.org/wiki/Table_of_spherical_harmonics#Real_spherical_harmonics]
        
        # initialization
        if ao_i==0:
            mo_coefficient_list_for_reordering=[]
            current_ang_mom=-1

        # read ang_mom (i.e., angular momentum of the shell)
        ang_mom=basis_shell_ang_mom[ao_index]
        previous_ang_mom=current_ang_mom
        current_ang_mom=ang_mom
        
        # set multiplicity
        multiplicity = 2 * ang_mom + 1
        print(f"multiplicity = {multiplicity}")
        
        # check if the buffer is null, when ang_mom changes
        if previous_ang_mom != current_ang_mom:
            assert len(mo_coefficient_list_for_reordering) == 0
        
        if current_ang_mom==0: # s shell
            print("s shell/no permutation is needed.")
            print("(trexio  notation): s(l=0)")
            print("(makefun notation): s(l=0)")
            reorder_index=[0]
        
        elif current_ang_mom==1: # p shell
            
            if ao_cartesian!=0:
                print("p shell/no permutation is needed.")
                print("(trexio  notation): px(l=+1), py(l=-1), pz(l=0)")
                print("(makefun notation): px(l=+1), py(l=-1), pz(l=0)")
                reorder_index=[0,1,2]
            else:
                print("p shell/permutation is needed.")
                print("(trexio  notation): pz(l=0), px(l=+1), py(l=-1)")
                print("(makefun notation): px(l=+1), py(l=-1), pz(l=0)")
                reorder_index=[1,2,0]

        elif current_ang_mom==2: # d shell
            
            if ao_cartesian!=0:
                print("Cartesian notation for d shell is not implemented yet! Sorry.")
                raise NotImplemented
            else:
                print("d shell/permutation is needed.")
                print("(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)")
                print("(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)")
                reorder_index=[0,3,4,2,1]
            
        elif current_ang_mom==3: # f shell
            
            if ao_cartesian!=0:
                print("Cartesian notation for f shell is not implemented yet! Sorry.")
                raise NotImplemented
            
            else:
                print("f shell/no permutation is needed.")
                print("(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)")
                print("(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)")
                reorder_index=[0,1,2,3,4,5,6]
            
        else:
            print("Not implemented")
            
        basis_index_list = [n for n, v in enumerate(basis_shell_index) if v == ao_index]
        
        mo_local_buffer=[]
        for basis_index in basis_index_list:
            mo_local_buffer.append(mo_coefficient[mo_i][ao_i]*basis_coefficient[basis_index])
        mo_coefficient_list_for_reordering.append(mo_local_buffer)

        # write MOs!!
        if len(mo_coefficient_list_for_reordering) == multiplicity:
            print("--write MOs!!--")
            mo_list_reordered=[mo_coefficient_list_for_reordering[i] for i in reorder_index]
            
            # reordered again is needed here for contracted shell!
            # because order is not px ... py ... pz but px,py,pz,px,py,pz ...
            for ii in range(len(mo_list_reordered[0])):
                for mo_coeff_list_reordered in mo_list_reordered:
                    mo_coefficient_list.append(mo_coeff_list_reordered[ii])
            
            # reset buffer
            mo_coefficient_list_for_reordering=[]
        
    mo_coefficient_turbo.append(mo_coefficient_list)


print("END")

basis set is represent with spherical
============1-th MO================
--ao_i=0, ao_index=0--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=1, ao_index=1--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=2, ao_index=2--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=3, ao_index=3--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=4, ao_index=4--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=5, ao_index=5--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=6, ao_index=6--
multiplicity = 1
s shell/no permutation

(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=23, ao_index=15--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=24, ao_index=15--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=25, ao_index=15--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=26, ao_index=16--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=27, ao_index=16--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=28, ao_index=16--
mu

(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=78, ao_index=37--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=79, ao_index=37--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=80, ao_index=37--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=81, ao_index=37--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--write MOs!!--

multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=101, ao_index=50--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--ao_i=102, ao_index=50--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--write MOs!!--
============13-th MO================
--ao_i=0, ao_index=0--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=1, ao_index=1--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
-

--write MOs!!--
--ao_i=71, ao_index=35--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=72, ao_index=35--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=73, ao_index=35--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=74, ao_index=36--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=75, ao_index=36--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=76, ao_index=36--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(m

...

s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=7, ao_index=7--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=8, ao_index=8--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=9, ao_index=9--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=10, ao_index=10--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=11, ao_index=11--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=12, ao_index=11--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1)

s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=10, ao_index=10--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--write MOs!!--
--ao_i=11, ao_index=11--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=12, ao_index=11--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=13, ao_index=11--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=14, ao_index=12--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=15, ao_index=12--
multiplicity = 3
p shell/permutat

--ao_i=53, ao_index=23--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notation): dz2(l=0), dx2-y2(l=+2), dxy(l=-2), dyz(l=-1), dzx=(l=+1)
--write MOs!!--
--ao_i=54, ao_index=24--
multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
--ao_i=55, ao_index=24--
multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
--ao_i=56, ao_index=24--
multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f

multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
--ao_i=59, ao_index=24--
multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
--ao_i=60, ao_index=24--
multiplicity = 7
f shell/no permutation is needed.
(trexio  notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
(makefun notation): f3,0(l=0), f3,+1(l=+1), f3,-1(l=-1), f3,+2(l=+2), f3,-2(l=-2), f3,+3(l=+3), f3,-3(l=-3)
--write MOs!!--
--ao_i=61, ao_index=25--
multiplicity = 1
s shell/no permutation is needed.
(trexio  notation): s(l=0)
(makefun notation): s(l=0)
--w

p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=40, ao_index=20--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=41, ao_index=21--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=42, ao_index=21--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--ao_i=43, ao_index=21--
multiplicity = 3
p shell/permutation is needed.
(trexio  notation): pz(l=0), px(l=+1), py(l=-1)
(makefun notation): px(l=+1), py(l=-1), pz(l=0)
--write MOs!!--
--ao_i=44, ao_index=22--
multiplicity = 5
d shell/permutation is needed.
(trexio  notation): dz2(l=0), dzx=(l=+1), dyz(l=-1), dx2-y2(l=+2), dxy(l=-2)
(makefun notati

In [81]:
from logging import config, getLogger, StreamHandler, Formatter
logger = getLogger("Turbo-Genius")
logger.setLevel("INFO")
stream_handler = StreamHandler()
stream_handler.setLevel("INFO")
handler_format = Formatter('%(name)s - %(levelname)s - %(lineno)d - %(message)s')
stream_handler.setFormatter(handler_format)
logger.addHandler(stream_handler)
io_fort10.f10detbasissets.mo_coefficient=mo_coefficient_turbo

Turbo-Genius.pyturbo.io_fort10 - INFO - 546 - 103
Turbo-Genius.pyturbo.io_fort10 - INFO - 546 - 103


CalledProcessError: Command 'line=`gsed -n 153p fort.10`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$3=-0.0012211264085020045}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$4=0.010101872174123117}1'`; gsed -i "153d" fort.10; gsed -i "153i \ $line" fort.10; line=`gsed -n 154p fort.10`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$1=-8.188895703370323e-05}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$2=-0.15138306991876113}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$3=-0.00687985915408193}1'`; gsed -i "154d" fort.10; gsed -i "154i \ $line" fort.10; line=`gsed -n 155p fort.10`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$1=0.2863672870747648}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$2=0.347554255188991}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$3=0.4792436313246424}1'`; gsed -i "155d" fort.10; gsed -i "155i \ $line" fort.10; line=`gsed -n 156p fort.10`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$1=0.07289296194859576}1'`; line=`echo $line |  awk '{FS=" ";OFS=" "}{$2=0.00295

In [74]:
# VMC calculation
vmc=VMC.parse_from_default_namelist()
vmc.generate_input()

Turbo-Genius.utils.utility - DEBUG - 115 - variable=2
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=150000
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=86400
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=1
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=True
Turbo-Genius.utils.utility - DEBUG - 115 - variable=1.0e-10
Turbo-Genius.utils.utility - DEBUG - 116 - isdecimal=False
Turbo-Genius.pyturbo.vmc - INFO - 58 - datasvmc.input has been generated. 

